### Importações

In [26]:
from functools import reduce
from pyspark.sql import SparkSession, Window
from pyspark.sql import types as T
from pyspark.sql.functions import col, when
from pyspark.sql import functions as F 
import kagglehub
import shutil
import os
import re
import pandas as pd
import plotly.express as px

### Iniciando o Spark

In [2]:
spark = SparkSession.builder \
    .master("local[*]") \
    .config("spark.ui.port", "4040") \
    .getOrCreate()

spark.sparkContext.setLogLevel("ERROR") 
spark

your 131072x1 screen size is bogus. expect trouble
26/01/06 21:01:30 WARN Utils: Your hostname, NB74484S resolves to a loopback address: 127.0.1.1; using 172.18.143.78 instead (on interface eth0)
26/01/06 21:01:30 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
26/01/06 21:01:31 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


### Fazendo o download do arquivo

In [8]:
# Força o download do dataset
download_path = kagglehub.dataset_download("sudalairajkumar/novel-corona-virus-2019-dataset", force_download=True)

# Define o destino
destination_path = "../data/raw"
os.makedirs(destination_path, exist_ok=True)

# Nome do arquivo principal
target_file = "time_series_covid_19_confirmed"
target_path = os.path.join(destination_path, target_file)

# Verifica se já existe
if not os.path.exists(target_path):
    for file in os.listdir(download_path):
        shutil.move(os.path.join(download_path, file), destination_path)
    print("Arquivos movidos para:", destination_path)
else:
    print("Arquivo já baixado:", destination_path)

100%|██████████| 8.52M/8.52M [00:01<00:00, 8.46MB/s]

Extracting files...


Arquivos movidos para: ../data/raw


### Lendo os arquivos usando o Spark

In [9]:
df_confirmed_cases = spark \
    .read \
    .format("csv") \
    .option("delimiter", ",") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load("../data/raw/time_series_covid_19_confirmed.csv")
    
df_confirmed_cases.show(5)        

+--------------+--------------+--------+---------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--

In [10]:
df_confirmed_deaths = spark \
    .read \
    .format("csv") \
    .option("delimiter", ",") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load("../data/raw/time_series_covid_19_deaths.csv")
    
df_confirmed_deaths.show(5)        

+--------------+--------------+--------+---------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+------+------+------+------+------+------+------+------+------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--

### Deixando mais visível como ver as colunas

In [11]:
df_confirmed_cases_cols = df_confirmed_cases.columns
total_cols_to_display = 6

for i in range(0, len(df_confirmed_cases_cols), total_cols_to_display):
    df_confirmed_cases.select(df_confirmed_cases_cols[i:i+total_cols_to_display]).show(5)

+--------------+--------------+--------+---------+-------+-------+
|Province/State|Country/Region|     Lat|     Long|1/22/20|1/23/20|
+--------------+--------------+--------+---------+-------+-------+
|          NULL|   Afghanistan|33.93911|67.709953|      0|      0|
|          NULL|       Albania| 41.1533|  20.1683|      0|      0|
|          NULL|       Algeria| 28.0339|   1.6596|      0|      0|
|          NULL|       Andorra| 42.5063|   1.5218|      0|      0|
|          NULL|        Angola|-11.2027|  17.8739|      0|      0|
+--------------+--------------+--------+---------+-------+-------+
only showing top 5 rows

+-------+-------+-------+-------+-------+-------+
|1/24/20|1/25/20|1/26/20|1/27/20|1/28/20|1/29/20|
+-------+-------+-------+-------+-------+-------+
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|     

In [12]:
df_confirmed_deaths_cols = df_confirmed_deaths.columns
total_cols_to_display = 6

for i in range(0, len(df_confirmed_deaths_cols), total_cols_to_display):
    df_confirmed_deaths.select(df_confirmed_deaths_cols[i:i+total_cols_to_display]).show(5)

+--------------+--------------+--------+---------+-------+-------+
|Province/State|Country/Region|     Lat|     Long|1/22/20|1/23/20|
+--------------+--------------+--------+---------+-------+-------+
|          NULL|   Afghanistan|33.93911|67.709953|      0|      0|
|          NULL|       Albania| 41.1533|  20.1683|      0|      0|
|          NULL|       Algeria| 28.0339|   1.6596|      0|      0|
|          NULL|       Andorra| 42.5063|   1.5218|      0|      0|
|          NULL|        Angola|-11.2027|  17.8739|      0|      0|
+--------------+--------------+--------+---------+-------+-------+
only showing top 5 rows

+-------+-------+-------+-------+-------+-------+
|1/24/20|1/25/20|1/26/20|1/27/20|1/28/20|1/29/20|
+-------+-------+-------+-------+-------+-------+
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|      0|      0|      0|      0|
|      0|      0|     


### Objetivo da transformação dos dados

Nesta etapa, iremos **pivotar as colunas de datas**, garantindo que **todas as datas fiquem concentradas em uma única coluna chamada `data`**.  
Além disso, será criada uma coluna adicional chamada **`ano`**, extraída a partir da data correspondente, com o objetivo de melhorar a **visualização, análise temporal e organização dos dados**.

Cada mês será corretamente associado ao seu respectivo número, conforme a convenção abaixo:

- 1 — Janeiro  
- 2 — Fevereiro  
- 3 — Março  
- 4 — Abril  
- 5 — Maio  
- 6 — Junho  
- 7 — Julho  
- 8 — Agosto  
- 9 — Setembro  
- 10 — Outubro  
- 11 — Novembro  
- 12 — Dezembro  

### Formatos de data

Para atender diferentes necessidades de uso, serão mantidos **dois formatos de data no conjunto de dados**:

- Uma coluna de data no formato **string** (texto), preservando o valor original.
- Uma coluna de data no formato **date**, padronizada como **`yyyy-MM-dd`**, adequada para filtros, comparações e análises temporais.

Essa abordagem garante maior flexibilidade para análises, visualizações e integrações com outras ferramentas ou camadas do pipeline de dados.


In [13]:
# 1) Detectar colunas que são datas (padrão M/d/yy ou M/d/yyyy)
date_regex = r'^\d{1,2}/\d{1,2}/\d{2,4}$'
date_cols = [c for c in df_confirmed_cases_cols if re.match(date_regex, c)]
id_cols = [c for c in df_confirmed_cases_cols if c not in date_cols]  # chaves/atributos

# 2) Criar um map "data_str -> valor" e explodir
date_keys_arr = F.array(*[F.lit(c) for c in date_cols])
date_vals_arr = F.array(*[F.coalesce(F.col(c).cast("double"), F.lit(0.0)) for c in date_cols])  # trata nulos
m = F.map_from_arrays(date_keys_arr, date_vals_arr)

long_df_confirmed_cases = (
    df_confirmed_cases
    .select(*id_cols, F.explode(m).alias("data_str", "valor"))
    .withColumn("data",
        F.coalesce(
            F.to_date("data_str", "M/d/yy"),
            F.to_date("data_str", "M/d/yyyy"),
            F.to_date("data_str", "d/M/yy"),
            F.to_date("data_str", "d/M/yyyy"),
        )
    )
    .filter(F.col("data").isNotNull())
    .withColumn("ano", F.year("data"))
    .withColumn("mes", F.month("data"))
)
long_df_confirmed_cases.show(5)

+--------------+--------------+--------+---------+--------+-----+----------+----+---+
|Province/State|Country/Region|     Lat|     Long|data_str|valor|      data| ano|mes|
+--------------+--------------+--------+---------+--------+-----+----------+----+---+
|          NULL|   Afghanistan|33.93911|67.709953| 1/22/20|  0.0|2020-01-22|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/23/20|  0.0|2020-01-23|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/24/20|  0.0|2020-01-24|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/25/20|  0.0|2020-01-25|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/26/20|  0.0|2020-01-26|2020|  1|
+--------------+--------------+--------+---------+--------+-----+----------+----+---+
only showing top 5 rows



In [14]:
# 1) Detectar colunas que são datas (padrão M/d/yy ou M/d/yyyy)
date_regex = r'^\d{1,2}/\d{1,2}/\d{2,4}$'
date_cols = [c for c in df_confirmed_deaths_cols if re.match(date_regex, c)]
id_cols = [c for c in df_confirmed_deaths_cols if c not in date_cols]  # chaves/atributos

# 2) Criar um map "data_str -> valor" e explodir
date_keys_arr = F.array(*[F.lit(c) for c in date_cols])
date_vals_arr = F.array(*[F.coalesce(F.col(c).cast("double"), F.lit(0.0)) for c in date_cols])  # trata nulos
m = F.map_from_arrays(date_keys_arr, date_vals_arr)

long_df_confirmed_deaths = (
    df_confirmed_deaths
    .select(*id_cols, F.explode(m).alias("data_str", "valor"))
    .withColumn("data",
        F.coalesce(
            F.to_date("data_str", "M/d/yy"),
            F.to_date("data_str", "M/d/yyyy"),
            F.to_date("data_str", "d/M/yy"),
            F.to_date("data_str", "d/M/yyyy"),
        )
    )
    .filter(F.col("data").isNotNull())
    .withColumn("ano", F.year("data"))
    .withColumn("mes", F.month("data"))
)
long_df_confirmed_deaths.show(5)

+--------------+--------------+--------+---------+--------+-----+----------+----+---+
|Province/State|Country/Region|     Lat|     Long|data_str|valor|      data| ano|mes|
+--------------+--------------+--------+---------+--------+-----+----------+----+---+
|          NULL|   Afghanistan|33.93911|67.709953| 1/22/20|  0.0|2020-01-22|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/23/20|  0.0|2020-01-23|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/24/20|  0.0|2020-01-24|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/25/20|  0.0|2020-01-25|2020|  1|
|          NULL|   Afghanistan|33.93911|67.709953| 1/26/20|  0.0|2020-01-26|2020|  1|
+--------------+--------------+--------+---------+--------+-----+----------+----+---+
only showing top 5 rows




###  Agregação Mensal de Casos e Óbitos

A coluna **`soma_mes`** representa o total agregado de **casos confirmados** e **óbitos** por mês.  
Essa agregação tem como objetivo fornecer uma visão **global do volume mensal** de registros, considerando apenas o aspecto temporal.

- **Coluna analisada**: `soma_mes`  
- **Granularidade**: mensal  


In [15]:
totais_mes_confirmed_cases = (
    long_df_confirmed_cases
    .groupBy("ano", "mes", "Province/State", "Country/Region")
    .agg(F.sum("valor").alias("soma_mes"))
)
totais_mes_confirmed_cases.show(5)


+----+---+--------------------+--------------+--------+
| ano|mes|      Province/State|Country/Region|soma_mes|
+----+---+--------------------+--------------+--------+
|2020|  4|     South Australia|     Australia| 12734.0|
|2020|  9|Prince Edward Island|        Canada|  1630.0|
|2020| 12|             Beijing|         China| 29764.0|
|2020|  4|          Guadeloupe|        France|  4293.0|
|2020| 10|Falkland Islands ...|United Kingdom|   403.0|
+----+---+--------------------+--------------+--------+
only showing top 5 rows



In [16]:
totais_mes_confirmed_deaths = (
    long_df_confirmed_deaths
    .groupBy("ano", "mes", "Province/State", "Country/Region")
    .agg(F.sum("valor").alias("soma_mes"))
)
totais_mes_confirmed_deaths.show(5)


+----+---+--------------------+--------------+--------+
| ano|mes|      Province/State|Country/Region|soma_mes|
+----+---+--------------------+--------------+--------+
|2020|  4|     South Australia|     Australia|    88.0|
|2020|  9|Prince Edward Island|        Canada|     0.0|
|2020| 12|             Beijing|         China|   279.0|
|2020|  4|          Guadeloupe|        France|   271.0|
|2020| 10|Falkland Islands ...|United Kingdom|     0.0|
+----+---+--------------------+--------------+--------+
only showing top 5 rows




### Comparação das Taxas de Letalidade e Incidência

Nesta etapa, será realizada a comparação entre a **taxa de letalidade** (razão entre o número de mortes e o número de casos) e a **relação inversa**, que representa a quantidade de **casos associados a cada ocorrência de morte**.

A **taxa de letalidade** é calculada pela razão:

- **Mortes / Casos**

Essa métrica indica a proporção de casos confirmados que resultaram em óbito, permitindo avaliar a **gravidade da doença ao longo do período analisado**.

De forma complementar, será analisada também a razão inversa:

- **Casos / Mortes**

Essa relação expressa quantos casos, em média, estão associados a cada morte registrada, auxiliando na compreensão da **ocorrência e impacto dos óbitos em relação ao volume total de casos**.


In [17]:
df_mortes_prep = totais_mes_confirmed_deaths.withColumnRenamed("soma_mes", "total_mortes")
df_casos_prep = totais_mes_confirmed_cases.withColumnRenamed("soma_mes", "total_casos")

df_comparativo = df_mortes_prep.join(
    df_casos_prep, 
    on=["ano", "mes", "Country/Region"], 
    how="inner"
)

In [19]:
# Após o join, selecione explicitamente o que você quer
df_resultado = df_comparativo.select(
    "Country/Region", 
    "ano", 
    "mes", 
    "total_mortes", 
    "total_casos"
)

# Agora crie as colunas de cálculo
df_resultado = df_resultado.withColumn(
    "taxa_letalidade_pct", (F.col("total_mortes") / F.col("total_casos")) * 100
).withColumn(
    "casos_por_morte", F.col("total_casos") / F.col("total_mortes")
)

# Converta para Pandas e gere o gráfico
top_letalidade = df_resultado.orderBy(F.col("taxa_letalidade_pct").desc()).limit(10).toPandas()


In [20]:
# Países com maior número de casos por cada morte (menor letalidade aparente)
print("Países com mais casos para cada 1 morte:")
df_resultado.select("Country/Region", "ano", "mes", "total_casos", "total_mortes", "casos_por_morte") \
    .orderBy(F.col("casos_por_morte").desc()) \
    .show(10)

# Países com maior taxa de letalidade (%)
print("Países com maior taxa de letalidade:")
df_resultado.orderBy(F.col("taxa_letalidade_pct").desc()).show(10)


Países com mais casos para cada 1 morte:
+--------------+----+---+------------+------------+-----------------+
|Country/Region| ano|mes| total_casos|total_mortes|  casos_por_morte|
+--------------+----+---+------------+------------+-----------------+
|        France|2020| 11|   5.82896E7|         1.0|        5.82896E7|
|        France|2021|  5|1.64501011E8|        29.0|5672448.655172414|
|        France|2021|  4|1.54169338E8|        30.0|5138977.933333334|
|United Kingdom|2021|  5|1.28974466E8|        29.0|4447395.379310345|
|United Kingdom|2021|  5|1.28974466E8|        29.0|4447395.379310345|
|United Kingdom|2021|  4|1.31500537E8|        30.0|4383351.233333333|
|United Kingdom|2021|  4|1.31500537E8|        30.0|4383351.233333333|
|United Kingdom|2021|  3|1.32310463E8|        31.0|4268079.451612903|
|United Kingdom|2021|  3|1.32310463E8|        31.0|4268079.451612903|
|        France|2021|  3|1.27868432E8|        31.0|4124788.129032258|
+--------------+----+---+------------+-----------

### Identificação de Picos de Letalidade Mensal com Pandas e Plotly

Nesta etapa, garantimos que os dados estejam estruturados em um **Pandas DataFrame**, que é o padrão ouro para bibliotecas de visualização como o **Plotly**. 

*   **O que estamos buscando:** O mês específico em que cada país apresentou a menor proporção de `casos_por_morte` (ou seja, o momento em que a doença foi mais letal ou a testagem foi menor).
*   **Próximo Passo:** Após visualizar esses picos mensais, realizaremos a agregação (`sum`) para descobrir qual país acumulou o maior impacto total no ano de 2026

**Objetivo da Visualização:**
*   **Zonas de Alta Letalidade:** Cores mais intensas/escuras (poucos casos registrados para cada morte).
*   **Zonas de Alta Testagem ou Baixa Letalidade:** Cores mais claras (muitos casos registrados para cada morte).

O mesmo acontece para o caso de `taxa_letalidade_pct`.

In [28]:
fig = px.scatter(
    df_resultado, 
    x="total_casos",           # Eixo X
    y="total_mortes",          # Eixo Y
    color="casos_por_morte",   # Cor baseada na sua métrica (casos para cada 1 morte)
    hover_name="Country/Region", # Nome que aparece no topo do balão de informações
    hover_data=["ano", "mes"],  # Informações extras ao passar o mouse
    title="Análise de Letalidade: Casos vs Mortes",
    labels={
        "total_casos": "Total de Casos",
        "total_mortes": "Total de Mortes",
        "casos_por_morte": "Casos por 1 Morte"
    },
    color_continuous_scale=px.colors.sequential.Reds_r # Escala de cor (Invertida: menos casos/morte = mais vermelho)
)

# Ajusta o layout para ficar mais limpo
fig.update_layout(template="plotly_white")

fig.show()

In [27]:
fig = px.scatter(
    df_resultado, 
    x="total_casos",           # Eixo X
    y="total_mortes",          # Eixo Y
    color="taxa_letalidade_pct",   # Cor baseada na sua métrica (casos para cada 1 morte)
    hover_name="Country/Region", # Nome que aparece no topo do balão de informações
    hover_data=["ano", "mes"],  # Informações extras ao passar o mouse
    title="Análise de Letalidade: Por cada País",
    labels={
        "total_casos": "Total de Casos",
        "total_mortes": "Total de Mortes",
        "taxa_letalidade_pct": "Casos por 1 Morte"
    },
    color_continuous_scale=px.colors.sequential.Reds_r # Escala de cor (Invertida: menos casos/morte = mais vermelho)
)

# Ajusta o layout para ficar mais limpo
fig.update_layout(template="plotly_white")

fig.show()

Agora iremos fazer para o pais com mais morte e letalidade no total somando todos os meses.

In [ ]:
totais_pais_confirmed_cases = (
    long_df_confirmed_cases
    .groupBy("Country/Region")
    .agg(
        F.sum("valor").alias("total_casos_acumulado")
    )
    .orderBy(F.col("total_casos_acumulado").desc()) 
)

totais_pais_confirmed_cases.show(5)

+--------------+---------------------+
|Country/Region|total_casos_acumulado|
+--------------+---------------------+
|            US|        6.047736004E9|
|         India|         3.22695359E9|
|        Brazil|        2.653620509E9|
|        Russia|         9.30548859E8|
|        France|         8.55026731E8|
+--------------+---------------------+
only showing top 5 rows



In [29]:
totais_pais_confirmed_deaths = (
    long_df_confirmed_deaths
    .groupBy("Country/Region")
    .agg(
        F.sum("valor").alias("total_casos_acumulado")
    )
    .orderBy(F.col("total_casos_acumulado").desc()) # Opcional: ordena pelos maiores
)

totais_pais_confirmed_deaths.show(5)

+--------------+---------------------+
|Country/Region|total_casos_acumulado|
+--------------+---------------------+
|            US|         1.23616044E8|
|        Brazil|          7.2624584E7|
|         India|          4.4428093E7|
|        Mexico|          4.3006478E7|
|United Kingdom|          2.8928802E7|
+--------------+---------------------+
only showing top 5 rows



In [30]:
totais_casos = long_df_confirmed_cases.groupBy("Country/Region") \
    .agg(F.sum("valor").alias("total_casos"))

# 2. Consolidar Mortes
totais_mortes = long_df_confirmed_deaths.groupBy("Country/Region") \
    .agg(F.sum("valor").alias("total_mortes"))

# 3. Fazer o Join dos dois pelo País
df_final_paises = totais_casos.join(totais_mortes, on="Country/Region", how="inner")

# 4. Criar a métrica de letalidade acumulada para 2026
df_final_paises = df_final_paises.withColumn(
    "casos_por_morte", 
    F.col("total_casos") / F.col("total_mortes")
)

# Converter para Pandas para o Plotly
pdf_final = df_final_paises.toPandas()

In [31]:

fig = px.scatter(
    pdf_final, 
    x="total_casos", 
    y="total_mortes",
    color="casos_por_morte",      # Mostra a taxa de letalidade na cor
    size="total_mortes",           # Bolhas maiores para países com mais mortes
    hover_name="Country/Region",
    text="Country/Region",         # Exibe o nome do país direto no ponto
    title="Ranking Global: Total de Casos vs. Total de Mortes (Acumulado 2026)",
    labels={
        "total_casos": "Volume Total de Casos",
        "total_mortes": "Volume Total de Mortes",
        "casos_por_morte": "Casos para cada 1 óbito"
    },
    color_continuous_scale=px.colors.sequential.YlOrRd_r # Amarelo para Vermelho (invertido)
)

# Ajustar posição do texto para não sobrepor o ponto
fig.update_traces(textposition='top center')
fig.update_layout(template="plotly_dark", height=700)

fig.show()
